<a href="https://colab.research.google.com/github/ciohl007/computer-vision/blob/main/Hough_Lines_in_OpenCV.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
title = "Computer Vision - Hough Transform in OpenCV"
email="jacky.baltes@ntnu.edu.tw"
author = """
<p>
      Jacky Baltes<br>
      National Taiwan Normal University<br>
      Taipei, Taiwan<br>
      <a href="mailto:{{email}}">{{email}}</a><br>
</p>
"""

from datetime import date
today = date.today().strftime("%d %B %Y")

In [ ]:
import subprocess
import pathlib
import os
import sys
import platform
from importlib import reload
import logging

logger = logging.getLogger(__name__)
logger.setLevel( logging.DEBUG )

try:
    GIT_CMD
except NameError:
    GIT_CMD = 'git'

try:
    cfg
except NameError:
    cfg = {}

class cd:
    """Context manager for changing the current working directory"""
    def __init__(self, newPath):
        self.newPath = pathlib.Path(newPath).expanduser().resolve()

    def __enter__(self):
        self.savedPath = pathlib.Path.cwd()
        os.chdir(self.newPath)

    def __exit__(self, etype, value, traceback):
        os.chdir(self.savedPath)

def updateGit( url, dirname, branch,  root ):
        with cd( root ):
            p = pathlib.Path( dirname )
            if ( branch ):
                bs = " --branch " + branch
            else:
                bs = ""
            if not p.is_dir():
                print("cloning {0} from url {1} root {2}".format( dirname, url, root ), 'git command', GIT_CMD)

                cmd = GIT_CMD + " clone " + bs + " " + url + " " + dirname
                os.system( cmd )
            else:
                logger.info("git directory exists")

            with cd( dirname ):
                logger.info("Executing git pull")
                o = None
                try:
                    o = subprocess.check_output(GIT_CMD + " pull", stderr=subprocess.STDOUT, shell=True)
                except subprocess.CalledProcessError:
                    pass
                if ( o ):
                    logger.info( 'git pull:' + o.decode('utf-8') )

updateGit('https://github.com/cvroberto21/NTNU-Lectures.git', 'NTNU-Lectures', 'mg', '.')

d = str( pathlib.Path( pathlib.Path('.') / 'NTNU-Lectures' ).resolve() )
if d not in sys.path:
    sys.path.append(  d )
logger.debug('System Path %s', sys.path)

import jblecture

jblecture = reload(jblecture)
node = platform.node()

# %reload_ext jblecture
jblecture.load_ipython_extension( get_ipython(), cfg )

from jblecture import addJBImage, addJBVideo, addJBData, addJBFigure, addJBGraph, addJBAnimation
from jblecture import addJBCharacter
from jblecture import createTable
from jblecture import instTemplate
from jblecture import _a
from jblecture import downloadDir, zipDirectory
from IPython.core.display import display, HTML, Math

doc = cfg['doc']
GDrive = None

import IPython
import uuid

def createRevealJSAndDownload():
    logger.info('Create reveal.js and download it')
    doc.createRevealDownload( cfg['REVEAL_DIR'] )
    downloadDir( cfg['ROOT_DIR'] / "{title}_reveal.zip".format( title=title ), "reveal.js", cfg['ROOT_DIR'] )

def finalize():
    cfg['TITLE'] = title

    doc.createRevealDownload( cfg['REVEAL_DIR'] )

    if jblecture.jbgithub.createGitHub( cfg['TITLE'], cfg['ROOT_DIR']):
        logger.debug("Successful upload of presentation")
        print("You can access the presentation at " + cfg['GITHUB_PAGES_URL'] )
    else:
        logger.warning("Upload of presentation failed")

# logging.getLogger().setLevel(logging.WARNING)

# jblecture.jbgithub.login( jblecture.jbgithub.readGithubToken() )
# if ( cfg['GITHUB'] ):
#     logging.info("Successful login to github")
# else:
#     logging.warning("Github integration disabled")

# This must come last

# class InvokeButton(object):

#     def __init__(self, title, callback):
#         self._title = titlea
#         self._callback = callback

#     def _repr_html_(self):
#         from google.colab import output
#         callback_id = 'button-' + str(uuid.uuid4())
#         output.register_callback(callback_id, self._callback)

#         template = """<button id="{callback_id}" style="height:3cm;">{title}</button>
#             <script>
#             document.querySelector("#{callback_id}").onclick = (e) => {{
#                 //IPython.notebook.execute_cells_after()
#                 google.colab.kernel.invokeFunction('{callback_id}', [], {{}})
#                 e.preventDefault();
#             }};
#             </script>"""
#         html = template.format(title=self._title, callback_id=callback_id)
#         return html

# InvokeButton('Create and Download Reveal.js Slideshow', createRevealJSAndDownload )




cloning NTNU-Lectures from url https://github.com/cvroberto21/NTNU-Lectures.git root . git command git


In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import math
import random

import cv2
from skimage import io

In [ ]:
%%slide --id=first
%%reveal_html

<h1> {{title}}</h1>

   <div class="author" style="text-align:center;">
    {{author}}
   </div>

In [ ]:
%%slide
%%reveal_html

<h1>Hough Detection in OpenCV</h1>

<div class="jb-text">
Detection of lines and circles using the <a href="http://www.opencv.org/">OpenCV</a> vision library.
</div>

In [ ]:
%%slide --echo

url = "https://i.postimg.cc/3rBpv96M/image.png" #@param {type:"string"}
img = io.imread( url )
img = cv2.resize(img, (640, 480 ) )

fig = plt.figure()
ax1 = fig.add_subplot(1,1,1)
ax1.set_title('Original Image')

ax1.imshow(img, interpolation = 'bicubic')
ax1.set_xticks([])
ax1.set_yticks([])

imgOrig = addJBFigure("imgOrig", 0, 0, fig )
plt.close()

In [ ]:
%%slide
%%reveal_html

<h1>Input Image</h1>

{{ imgOrig() }}

In [ ]:
%%slide --echo

kernel = 7 #@param ["3", "5", "7", "9", "11"] {type:"raw"}
fig = plt.figure()
ax1 = fig.add_subplot(1,1,1)
ax1.set_title('Original Image')


gray = cv2.cvtColor( img,  cv2.COLOR_RGB2GRAY );

ax1.imshow(gray, cmap='gray', interpolation = 'bicubic')
ax1.set_xticks([])
ax1.set_yticks([])

imgGray = addJBFigure( "imgGray", 0, 0, fig )
plt.close()


In [ ]:
%%slide
%%reveal_html

<h1>Input Image</h1>

{{ imgGray() }}

In [ ]:
%%slide --echo

canny = cv2.Canny( img, 100, 300, 3 )

fig = plt.figure()
ax = fig.add_subplot(1,1,1)
ax.set_title('Canny')
ax.set_xticks([])
ax.set_yticks([])

ax.imshow( canny, cmap = 'gray')

imgEdge = addJBFigure("imgEdge", 0, 0, fig )

plt.close()

In [ ]:
%%slide
%%reveal_html

<h1>Canny Edge Detection</h1>

{{ imgEdge() }}

In [ ]:
%%slide --echo

draw = img.copy()

rhoAccuracy = 2
thetaAccuracy = np.pi/180.0
minVotes = 200

lines = cv2.HoughLines( canny, rhoAccuracy, thetaAccuracy, minVotes)
if ( lines is not None ):
  print("Number of lines found", len(lines))
  for line in lines:
    for rho,theta in line:
      a = np.cos(theta)
      b = np.sin(theta)
      x0 = a*rho
      y0 = b*rho
      x1 = int(x0 + 1000*(-b))
      y1 = int(y0 + 1000*(a))
      x2 = int(x0 - 1000*(-b))
      y2 = int(y0 - 1000*(a))

      cv2.line(draw,(x1,y1),(x2,y2),(0,0,255),2)

fig = plt.figure()
ax = fig.add_subplot(1,1,1)
ax.set_title('Hough Lines')
ax.set_xticks([])
ax.set_yticks([])

ax.imshow( draw, cmap = 'gray')

imgLinesH = addJBFigure("imgLinesH", 0, 0, fig )
plt.close()


In [ ]:
%%slide
%%reveal_html

<h1>Hough Lines Output</h1>

{{ imgLinesH() }}



In [ ]:
%%slide --echo

draw = img.copy()

rhoAccuracy = 5
thetaAccuracy = np.pi/45.0
minVotes = 400
minLineLength = 300
maxLineGap = 0

lines = cv2.HoughLinesP( canny, rhoAccuracy, thetaAccuracy, minVotes, minLineLength, maxLineGap)
if ( lines is not None ):
  print("Found number of lines", len(lines) )
  for line in lines:
    for x1,y1,x2,y2 in line:
      cv2.line(draw,(x1,y1),(x2,y2),(0,0,255),2)

fig = plt.figure()
ax = fig.add_subplot(1,1,1)
ax.set_title('Hough Lines')
ax.set_xticks([])
ax.set_yticks([])

ax.imshow( draw, cmap = 'gray')

imgLinesP = addJBFigure( "imgLinesP", 0, 0, fig)
plt.close()


In [ ]:
%%slide
%%reveal_html

<h1>Probabilistic Hough Line Segements using <code>HoughLinesP</code></h1>

{{ imgLinesP() }}

In [ ]:
finalize()

INFO:jblecture.jbgithub:Github repo ntnu-erc-test
INFO:jblecture.jbgithub:Github repo gacr-most-ctu-ntnu
INFO:jblecture.jbgithub:Github repo Lecture-VN
INFO:jblecture.jbgithub:Github repo -title-
INFO:jblecture.jbgithub:Github repo A--Search
INFO:jblecture.jbgithub:Github repo A--Search-Introduction
INFO:jblecture.jbgithub:Github repo A-Star-Search-Introduction
INFO:jblecture.jbgithub:Github repo acpr_rv_2019
INFO:jblecture.jbgithub:Github repo advanced_ai
INFO:jblecture.jbgithub:Github repo AkariMaker
INFO:jblecture.jbgithub:Github repo Artificial-Intelligence
INFO:jblecture.jbgithub:Github repo Artificial-Intelligence-and-Search
INFO:jblecture.jbgithub:Github repo Ax12-Motor-Tester
INFO:jblecture.jbgithub:Github repo BBC-Puzzle-for-Today--314-Upside-Down-Numbers
INFO:jblecture.jbgithub:Github repo BBC-Puzzle-for-Today-314-Upside-Down-Numbers
INFO:jblecture.jbgithub:Github repo Breadth-First-Search
INFO:jblecture.jbgithub:Github repo Camera-Calibration
INFO:jblecture.jbgithub:Github r

repo.name Computer-Vision---Hough-Transform https://github.com/jackybaltes/Computer-Vision---Hough-Transform.git
Contents [ContentFile(path="README.md")]
Creating branch gh-pages
Checking out branch gh-pages
Asset robbi Size 12677 Name /content/BuildDir/reveal.js/assets/images/robbi.png
Copying asset robbi /content/BuildDir/reveal.js/assets/images/robbi.png
Running command git add assets/images/robbi.png
Asset logo Size 12033 Name /content/BuildDir/reveal.js/assets/images/logo.png
Copying asset logo /content/BuildDir/reveal.js/assets/images/logo.png
Running command git add assets/images/logo.png
Asset fira-logo-1 Size 93836 Name /content/BuildDir/reveal.js/assets/images/FIRA-logo-1.png
Copying asset fira-logo-1 /content/BuildDir/reveal.js/assets/images/FIRA-logo-1.png
Running command git add assets/images/FIRA-logo-1.png
Asset pairLogo Size 63051 Name /content/BuildDir/reveal.js/assets/images/pairLogo.png
Copying asset pairLogo /content/BuildDir/reveal.js/assets/images/pairLogo.png
Run

DEBUG:__main__:Successful upload of presentation


You can access the presentation at https://jackybaltes.github.io/Computer-Vision---Hough-Transform/
